# Final Project: Battle of Neighborhoods

# 1 - Introduction

On the mist of the new COVID pandemic, understanding of its effects on different communities and its spread mechanisms is essential for planning and strategy development. One of the main difficulties of the task is to explicitly define the relevant variables and parameters to inspect, as a lot of different factors are at play and we do not exactly understand their influence. The following study, although modest, pretends to explore the spread of the disease on different communities hoping to find patterns or clues regarding its behaviour. While the most natural assumption would be that the majority of the infections occur on densely populated areas, we want to assess the nature of the neighborhoods instead, trying to conclude whether the dominant presence of social hubs, comercial districts or open areas conveys a significant difference in numbers.

## 2 - Data

We will study data from two cities, New York in USA and Toronto in Canada. We will extend the analysis of Manhattan from the course to the rest of the city and compare the results with the ones from Toronto. 
More explicitly, after obtaining the neighborhood list of both cities from an external database, we access access Foursquare to obtain information of the venues of each, so we can later find similar zones by clustering algorithms. At this point we will discuss differences and similarities between both cities. Later, using open access data from their respective official city portals, we will try to relate the incidence of COVID with the neighborhood clusters. Finally, we will compare the results on both financial capitals

## 3 - Methodology

### 3.1 - Libraries

In [2]:
import numpy as np 
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
!pip install -U folium
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import json # library to handle JSON files
import folium # map rendering library

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.5

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    openssl-1.1.1h             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-2.0.0

### 3.2 - New York

#### 3.2.1 - Geographical data

We start by extending the analysis of Manhattan from the course to the entire city. As before, we obtain the data from a json file from the url provided on the labs:

In [3]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json

In [4]:
#open file and name it newyork_data:
with open('newyork_data.json') as json_data:
    nydata = json.load(json_data)

In [5]:
#create a list from the json file
neibas = nydata['features']

In [6]:
# define columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# create dataframe
neighny = pd.DataFrame(columns=column_names)

In [7]:
#fill dataframe
for data in neibas:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighny = neighny.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Our initial table is:

In [8]:
neighny.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

and we use the `geolocator` package for the coordinates of the city as a whole:

In [9]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### 3.2.2 - Venue data

Now we obtain the venue data for each neighborhood. We start with our Foursquare credentials and the function introduced on the previous lab:

In [10]:
#bring data from foursquare
CLIENT_ID = 'VB4OF5HWVSRWUAR0IDA5TYRXPN2AXMT22RLCBE13QSCSMOLF' # your Foursquare ID
CLIENT_SECRET = '3TR140ED3YZFJCEMOCFNIM2ENRXONHZRIN4QFKFLJ32MBDET' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

In [11]:
#Finds the closest restaurants (100 at the most, <500 m) from each neighborhood's center,
#for all neighborhoods
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT = 100):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [12]:
#use the function above to make a dataframe from the retrieved Foursquare data
hoodsny = getNearbyVenues(names=neighny['Neighborhood'],
                                   latitudes=neighny['Latitude'],
                                   longitudes=neighny['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [13]:
#check dimensions and head of dataframe:
print(hoodsny.shape)
hoodsny.groupby('Neighborhood').count().head()

(10132, 7)


Neighbourhood Latitude  Neighbourhood Longitude  Venue  \
Neighborhood                                                            
Allerton                           31                       31     31   
Annadale                           11                       11     11   
Arden Heights                       5                        5      5   
Arlington                           6                        6      6   
Arrochar                           22                       22     22   

               Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                    
Allerton                   31               31              31  
Annadale                   11               11              11  
Arden Heights               5                5               5  
Arlington                   6                6               6  
Arrochar                   22               22              22

#### 3.2.3 - Clustering

We start preparing for our classification task:

In [24]:
#dummies dataframe
dummies = pd.get_dummies(hoodsny[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
dummies['Neighborhood'] = hoodsny['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [dummies.columns[-1]] + list(dummies.columns[:-1])
dummies = dummies[fixed_columns]

print(dummies.shape)
dummies.head()

(10132, 430)


Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0          0         0            0           0              0   
1      0          0         0            0           0              0   
2      0          0         0            0           0              0   
3      0          0         0            0           0              0   
4      0          0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0 

then we group by neighborhood and score each venue:

In [25]:
groupedny = dummies.groupby('Neighborhood').mean().reset_index()
print(groupedny.shape)
groupedny.head()

(302, 430)


Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0       Allerton          0.0                0.0             0.0   
1       Annadale          0.0                0.0             0.0   
2  Arden Heights          0.0                0.0             0.0   
3      Arlington          0.0                0.0             0.0   
4       Arrochar          0.0                0.0             0.0   

   Afghan Restaurant  African Restaurant  Airport Terminal  \
0                0.0                 0.0               0.0   
1                0.0                 0.0               0.0   
2                0.0                 0.0               0.0   
3                0.0                 0.0               0.0   
4                0.0                 0.0               0.0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0             0.000000           0.0     0.0               0.0   
1             0.181818           0.0     0.0               0.0   
2             0.000000           0.0     0.0               0.0   
3             0.000000           0.0     0.0               0.0   
4             0.000000           0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0               0.0            0.000000         0.0   
1                   0.0               0.0            0.000000         0.0   
2                   0.0               0.0            0.000000         0.0   
3                   0.0               0.0            0.000000         0.0   
4                   0.0               0.0            0.045455         0.0   

   Australian Restaurant  Austrian Restaurant  Auto Garage  Automotive Shop  \
0                    0.0                  0.0          0.0              0.0   
1                    0.0                  0.0          0.0              0.0   
2                    0.0                  0.0          0.0              0.0   
3                    0.0                  0.0          0.0              0.0   
4                    0.0                  0.0          0.0              0.0   

   BBQ Joint  Baby Store  Bagel Shop    Bakery  Bank  Bar  Baseball Field  \
0        0.0         0.0    0.000000  0.032258   0.0  0.0             0.0   
1        0.0         0.0    0.000000  0.000000   0.0  0.0             0.0   
2        0.0         0.0    0.000000  0.000000   0.0  0.0             0.0   
3        0.0         0.0    0.000000  0.000000   0.0  0.0             0.0   
4        0.0         0.0    0.045455  0.000000   0.0  0.0             0.0   

   Baseball Stadium  Basketball Court  Bath House     Beach  Beach Bar  \
0               0.0               0.0         0.0  0.000000        0.0   
1               0.0               0.0         0.0  0.000000        0.0   
2               0.0               0.0         0.0  0.000000        0.0   
3               0.0               0.0         0.0  0.000000        0.0   
4               0.0               0.0         0.0  0.045455        0.0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0       0.0          0.0         0.0            0.0                       0.0   
1       0.0          0.0         0.0            0.0                       0.0   
2       0.0          0.0         0.0            0.0                       0.0   
3       0.0          0.0         0.0            0.0                       0.0   
4       0.0          0.0         0.0            0.0                       0.0   

   Bike Shop  Bike Trail  Bistro  Board S

we use a previously defined function once more, for the top venues of each neighborhood:

In [26]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# ---------------------------------
# create a new dataframe
topvenuesny = pd.DataFrame(columns=columns)
topvenuesny['Neighborhood'] = groupedny['Neighborhood']

for ind in np.arange(topvenuesny.shape[0]):
    topvenuesny.iloc[ind, 1:] = return_most_common_venues(groupedny.iloc[ind, :], num_top_venues)

print(topvenuesny.shape)
topvenuesny.head()

(302, 11)


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place    Chinese Restaurant   
1       Annadale   American Restaurant           Pizza Place   
2  Arden Heights         Deli / Bodega              Pharmacy   
3      Arlington         Deli / Bodega           Coffee Shop   
4       Arrochar              Bus Stop    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Discount Store         Deli / Bodega                   Spa   
1          Dance Studio         Train Station                  Food   
2           Coffee Shop              Bus Stop           Pizza Place   
3              Bus Stop          Home Service         Boat or Ferry   
4         Deli / Bodega           Supermarket                 Beach   

       6th Most Common Venue       7th Most Common Venue  \
0                Supermarket       Check Cashing Service   
1                      Diner                  Restaurant   
2              Women's Store  Financial or Legal Service   
3              Grocery Store               Women's Store   
4  Middle Eastern Restaurant                    Pharmacy   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Electronics Store   Martial Arts School               Pharmacy  
1                  Park         Deli / Bodega     Falafel Restaurant  
2            Eye Doctor               Factory     Falafel Restaurant  
3     Fish & Chips Shop               Factory     Falafel Restaurant  
4          Liquor Store            Bagel Shop         Sandwich Place

Finally, we obtain clusters:

In [27]:
# set number of clusters
kclusters = 4
Clusters = groupedny.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Clusters)

# check labels
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 1, 1, 1, 1, 1], dtype=int32)

In [28]:
# add labels
topvenuesny.insert(0, 'Cluster Labels', kmeans.labels_)
        
#merge initial table (boroughs, neighs, lat, long) with the final one:
nyfinal = neighny
nyfinal = nyfinal.join(topvenuesny.set_index('Neighborhood'), on='Neighborhood')

#As not all neighs returned venues, nyfinal has less rows than table
nyfinal.dropna(subset=['Cluster Labels'], inplace=True)
print(nyfinal.shape)
nyfinal.head()

(306, 15)


Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               0   
1   Bronx   Co-op City  40.874294 -73.829939               1   
2   Bronx  Eastchester  40.887556 -73.827806               0   
3   Bronx    Fieldston  40.895437 -73.905643               1   
4   Bronx    Riverdale  40.890834 -73.912585               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy          Dessert Shop           Pizza Place   
1           Bus Station                   Bar  Fast Food Restaurant   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3                 Plaza  Medical Supply Store                 River   
4                  Park            Playground                  Bank   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Donut Shop            Laundromat           Gas Station   
1                 Trail                  Park           Pizza Place   
2                 Diner     Convenience Store         Metro Station   
3         Women's Store               Exhibit            Eye Doctor   
4                 Plaza                   Gym         Moving Target   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop         Deli / Bodega        Sandwich Place   
1         Grocery Store            Bagel Shop            Restaurant   
2    Seafood Restaurant  Fast Food Restaurant    Chinese Restaurant   
3               Factory    Falafel Restaurant                  Farm   
4           Bus Station            Food Truck          Home Service   

  10th Most Common Venue  
0     Falafel Restaurant  
1     Chinese Restaurant  
2        Automotive Shop  
3         Farmers Market  
4                Factory

#### 3.2.3 - COVID data

We use the official city goverment site https://www1.nyc.gov/site/doh/covid/covid-19-data-boroughs.page; a huge repository of data is available on https://github.com/nychealth/coronavirus-data. As we want to relate the incidence of corona with the overall neighborhood activity, we focus on the geographical data and the case counts.

In [29]:
url = 'https://raw.githubusercontent.com/nychealth/coronavirus-data/master/data-by-modzcta.csv'
ny=pd.read_csv(url)
ny.head()

MODIFIED_ZCTA                        NEIGHBORHOOD_NAME BOROUGH_GROUP  \
0          10001               Chelsea/NoMad/West Chelsea     Manhattan   
1          10002                Chinatown/Lower East Side     Manhattan   
2          10003  East Village/Gramercy/Greenwich Village     Manhattan   
3          10004                       Financial District     Manhattan   
4          10005                       Financial District     Manhattan   

   COVID_CASE_COUNT  COVID_CASE_RATE  POP_DENOMINATOR  COVID_DEATH_COUNT  \
0               459          1947.97         23563.03                 27   
1              1371          1786.19         76755.41                161   
2               584          1085.47         53801.62                 35   
3                45          1232.67          3650.61                  1   
4               109          1298.22          8396.11                  2   

   COVID_DEATH_RATE  PERCENT_POSITIVE  TOTAL_COVID_TESTS  
0            114.59              5.53               8299  
1            209.76              6.61              20729  
2             65.05              3.07              19041  
3             27.39              4.43               1015  
4             23.82              4.24               2569

As it can be seen from the table above, the neighborhood division is different to ours. Because of population level and other demographic factors, some of the areas are lumped together, creating the 'Modified ZCTA' column. For further details consult the aforementioned repository. To deal with this, we will extract again geographical data from a json file and we will 'draw on top' of our map of clusters.

In [30]:
#get file, open it and name it
!wget -q -O 'nytopo.json' https://raw.githubusercontent.com/nychealth/coronavirus-data/master/Geography-resources/MODZCTA_2010_WGS1984.topo.json
    
with open('nytopo.json') as json_data:
    crownny = json.load(json_data)

In [31]:
crownny

{'type': 'Topology',
 'objects': {'collection': {'type': 'GeometryCollection',
   'geometries': [{'type': 'Polygon',
     'properties': {'MODZCTA': 10001, 'label': '10001, 10118'},
     'arcs': [[0, 1, 2, 3]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10002, 'label': 10002},
     'arcs': [[4, 5, 6, 7, 8, 9]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10003, 'label': 10003},
     'arcs': [[-7, 10, 11, 12, 13]]},
    {'type': 'MultiPolygon',
     'properties': {'MODZCTA': 10004, 'label': 10004},
     'arcs': [[[14, 15]], [[16, 17, 18, 19, 20]]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10005, 'label': 10005},
     'arcs': [[-19, 21, 22, -15, 23]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10006, 'label': 10006},
     'arcs': [[-18, 24, 25, 26, -22]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10007, 'label': 10007},
     'arcs': [[-26, 27, 28, 29]]},
    {'type': 'Polygon',
     'properties': {'MODZCTA': 10009, 'label'

### 3.3 - Toronto

With exception of the initial steps, as the data sources are different, we procede as before:

### 3.3.1 - Geographical data

In [32]:
#libs we need
!pip install html5lib
!pip install lxml
!pip install beautifulSoup4

import html5lib
import lxml
from bs4 import BeautifulSoup

     |████████████████████████████████| 5.5MB 2.9MB/s eta 0:00:01     |███████████████████████████▎    | 4.7MB 2.9MB/s eta 0:00:01
     |████████████████████████████████| 122kB 3.0MB/s eta 0:00:01


In [33]:
#bring data
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
table=pd.read_html(url, flavor='html5lib')[0]
table.head()

Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

preprocessing:

In [34]:
#keep everything without 'Non assigned' on 'Borough"
table=table[table.Borough != 'Not assigned'].reset_index()
table=table[['Postal Code','Borough','Neighbourhood']] #get rid of old index

print(table.shape)
table.head()

(103, 3)


Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

for the coordinates, from the lab:

In [35]:
df=pd.read_csv('https://cocl.us/Geospatial_data')
df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

we add the coordinates to the table; notice they are ordered differently

In [36]:
for x in table['Postal Code']:
    for y in df['Postal Code']:
        if x==y:
            table['Latitude']=df['Latitude']
            
for x in table['Postal Code']:
    for y in df['Postal Code']:
        if x==y:
            table['Longitude']=df['Longitude']
            
table.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.806686 -79.194353  
1  43.784535 -79.160497  
2  43.763573 -79.188711  
3  43.770992 -79.216917  
4  43.773136 -79.239476

### 3.3.2 - Venue data

and apply it to all neighborhoods on our table:

In [37]:
#new table with all neighboourhoods in Toronto (we increase the radius, as Toronto is smaller than NY)
TorontoHoods = getNearbyVenues(names=table['Neighbourhood'],
                                   latitudes=table['Latitude'],
                                   longitudes=table['Longitude'],
                                   radius=1000)

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [38]:
print(TorontoHoods.shape)
TorontoHoods.rename(columns={'Neighborhood': 'Neighbourhood'}, inplace=True) #4square uses US english

(4874, 7)


dummy indices:

In [39]:
#dummies dataframe
Dummies = pd.get_dummies(TorontoHoods[['Venue Category']], prefix="", prefix_sep="")

#For some reason there's another 'Neighborhood' column, we drop it and add the correct one
Dummies.pop("Neighborhood")
Dummies.insert(0, 'Neighbourhood', TorontoHoods['Neighbourhood']) 

print(Dummies.shape)
Dummies.head()

(4874, 335)


Neighbourhood  Accessories Store  Afghan Restaurant  African Restaurant  \
0     Parkwoods                  0                  0                   0   
1     Parkwoods                  0                  0                   0   
2     Parkwoods                  0                  0                   0   
3     Parkwoods                  0                  0                   0   
4     Parkwoods                  0                  0                   0   

   Airport  American Restaurant  Amphitheater  Animal Shelter  Antique Shop  \
0        0                    0             0               0             0   
1        0                    0             0               0             0   
2        0                    0             0               0             0   
3        0                    0             0               0             0   
4        0                    0             0               0             0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0         0            0           0                    0                 0   
1         0            0           0                    0                 0   
2         0            0           0                    0                 0   
3         0            0           0                    0                 0   
4         0            0           0                    0                 0   

   Athletics & Sports  Auto Dealership  Auto Workshop  Automotive Shop  \
0                   0                0              0                0   
1                   0                0              0                0   
2                   0                0              0                0   
3                   0                0              0                0   
4                   0                0              0                0   

   BBQ Joint  Baby Store  Badminton Court  Bagel Shop  Bakery  Bank  Bar  \
0          0           0                0           0       0     0    0   
1          0           0                0           0       0     0    0   
2          0           0                0           0       0     1    0   
3          0           0                0           0       0     0    0   
4          0           0                0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  Beach Bar  \
0               0                 0                   0      0          0   
1               0                 0                   0      0          0   
2               0                 0                   0      0          0   
3               0                 0                   0      0          0   
4               0                 0                   0      0          0   

   Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  Bookstore  \
0         0           0                   0          0       0          0   
1         0           0                   0          0       0          0   
2         0           0                   0          0       0          0   
3         0           0                   0          0       0          0   
4         0           0                   0          0       0          0   

   Botanical Garden  Boutique  Bowling Alley  Boxing Gym  \
0                 0         0              0           0   
1                 0         0              0           0   
2                 0         0              0           0   
3                 0         0              0           0   
4                 0         0              0           0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0            

and group by neighboorhoods:

In [40]:
GroupedHoods = Dummies.groupby('Neighbourhood').mean().reset_index()
print(GroupedHoods.shape)
GroupedHoods.head()

(98, 335)


Neighbourhood  Accessories Store  \
0                                        Agincourt               0.01   
1                           Alderwood, Long Branch               0.00   
2  Bathurst Manor, Wilson Heights, Downsview North               0.00   
3                                  Bayview Village               0.00   
4                Bedford Park, Lawrence Manor East               0.00   

   Afghan Restaurant  African Restaurant  Airport  American Restaurant  \
0           0.000000                 0.0      0.0                 0.01   
1           0.000000                 0.0      0.0                 0.00   
2           0.000000                 0.0      0.0                 0.00   
3           0.037037                 0.0      0.0                 0.00   
4           0.000000                 0.0      0.0                 0.02   

   Amphitheater  Animal Shelter  Antique Shop  Aquarium  Art Gallery  \
0           0.0             0.0           0.0       0.0         0.01   
1           0.0             0.0           0.0       0.0         0.00   
2           0.0             0.0           0.0       0.0         0.00   
3           0.0             0.0           0.0       0.0         0.00   
4           0.0             0.0           0.0       0.0         0.01   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0         0.0                 0.02               0.0            0.010000   
1         0.0                 0.00               0.0            0.000000   
2         0.0                 0.00               0.0            0.000000   
3         0.0                 0.00               0.0            0.018519   
4         0.0                 0.00               0.0            0.000000   

   Auto Dealership  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0              0.0            0.0              0.0   0.000000         0.0   
1              0.0            0.0              0.0   0.000000         0.0   
2              0.0            0.0              0.0   0.000000         0.0   
3              0.0            0.0              0.0   0.018519         0.0   
4              0.0            0.0              0.0   0.010000         0.0   

   Badminton Court  Bagel Shop    Bakery      Bank   Bar  Baseball Field  \
0              0.0         0.0  0.040000  0.000000  0.05             0.0   
1              0.0         0.0  0.083333  0.083333  0.00             0.0   
2              0.0         0.0  0.000000  0.068966  0.00             0.0   
3              0.0         0.0  0.000000  0.018519  0.00             0.0   
4              0.0         0.0  0.030000  0.000000  0.00             0.0   

   Baseball Stadium  Basketball Stadium  Beach  Beach Bar  Beer Bar  \
0               0.0                 0.0    0.0       0.01      0.01   
1               0.0                 0.0    0.0       0.00      0.00   
2               0.0                 0.0    0.0       0.00      0.00   
3               0.0                 0.0    0.0       0.00      0.00   
4               0.0                 0.0    0.0       0.00      0.03   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Bookstore  \
0    0.000000                 0.0        0.0    0.00       0.00   
1    0.000000                 0.0        0.0    0.00       0.00   
2    0.000000                 0.0        0.0    0.00       0.00   
3    0.018519                 0.0        0.0    0.00       0.00   
4    0.000000                 0.0        0.0    0.01       0.01   

   Botanical Garden  Boutique  Bowling Alley  Boxing Gym  \
0               0.0       0.0            0.0         0.0   
1               0.0       0.0            0.0         0.0   
2               0.0       0.0            0.0         0.0   
3               0.0       0.0            0.0         0.0   
4               0.0       0.0            0.0         0.0   

   Brazilian Restaurant  Breakfast Spot   Brewery  Bridal Shop    Bridge  \
0                   0.0            0.01  0.010000     0.000000  0.000000   


most frequent venue categories:

In [41]:
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
HoodsTopVen = pd.DataFrame(columns=columns)
HoodsTopVen['Neighbourhood'] = GroupedHoods['Neighbourhood']

for ind in np.arange(HoodsTopVen.shape[0]):
    HoodsTopVen.iloc[ind, 1:] = return_most_common_venues(GroupedHoods.iloc[ind, :], num_top_venues)

print(HoodsTopVen.shape)
HoodsTopVen.head()

(98, 11)


Neighbourhood 1st Most Common Venue  \
0                                        Agincourt           Coffee Shop   
1                           Alderwood, Long Branch              Pharmacy   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village           Coffee Shop   
4                Bedford Park, Lawrence Manor East           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                   Bar                Bakery   
1     Convenience Store                  Café          Skating Rink   
2           Coffee Shop           Pizza Place           Supermarket   
3     Indian Restaurant         Grocery Store               Brewery   
4                  Café            Restaurant   Japanese Restaurant   

  5th Most Common Venue   6th Most Common Venue 7th Most Common Venue  \
0            Restaurant  Furniture / Home Store    Tibetan Restaurant   
1         Shopping Mall             Golf Course                  Bank   
2           Bridal Shop              Ski Chalet              Ski Area   
3    Turkish Restaurant       Afghan Restaurant         Shopping Mall   
4             Gastropub      Seafood Restaurant                Bakery   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0             Gift Shop        Sandwich Place                   Park  
1                  Park         Grocery Store                 Bakery  
2         Shopping Mall    Chinese Restaurant         Sandwich Place  
3          Burger Joint           Supermarket         Sandwich Place  
4    Italian Restaurant                 Hotel               Beer Bar

clustering analysis:

In [42]:
# set number of clusters
kclusters = 6
Clusters = GroupedHoods.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Clusters)

# check labels
kmeans.labels_[0:10] 

array([2, 1, 2, 2, 2, 3, 2, 2, 2, 2], dtype=int32)

In [43]:
# add labels
HoodsTopVen.insert(0, 'Cluster Labels', kmeans.labels_)
        
#merge initial table (boroughs, neighs, lat, long) with the final one:
FinalHoods = table
FinalHoods = FinalHoods.join(HoodsTopVen.set_index('Neighbourhood'), on='Neighbourhood')

#As not all neighs returned venues, FinalHoods has less rows than table
FinalHoods.dropna(subset=['Cluster Labels'], inplace=True)
print(FinalHoods.shape)
FinalHoods.head()

(102, 16)


Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  43.806686 -79.194353             2.0                 Trail   
1  43.784535 -79.160497             1.0            Playground   
2  43.763573 -79.188711             2.0           Pizza Place   
3  43.770992 -79.216917             5.0                  Park   
4  43.773136 -79.239476             2.0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0           Coffee Shop  Fast Food Restaurant           Supermarket   
1          Burger Joint    Italian Restaurant                  Park   
2                  Bank           Coffee Shop  Fast Food Restaurant   
3           Coffee Shop     Indian Restaurant     Mobile Phone Shop   
4              Pharmacy           Gas Station     Indian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                Garden    Chinese Restaurant                   Gym   
1        Breakfast Spot                  Food  Fast Food Restaurant   
2     Food & Drink Shop              Pharmacy            Beer Store   
3    Chinese Restaurant  Fast Food Restaurant        Farmers Market   
4                  Bank                Bakery   Fried Chicken Joint   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Restaurant                  Bank             Hobby Shop  
1     Elementary School           Escape Room   Ethiopian Restaurant  
2        Sandwich Place           Supermarket       Greek Restaurant  
3     Elementary School           Escape Room   Ethiopian Restaurant  
4          Burger Joint           Music Store   Caribbean Restaurant

### 3.3.3 - COVID data

This data also comes from the respective city goverment official website https://www.toronto.ca/home/covid-19/covid-19-latest-city-of-toronto-news/covid-19-status-of-cases-in-toronto/, particularly on https://drive.google.com/file/d/1jzH64LvFQ-UsDibXO0MOtvjbL2CvnV3N/view. As it was difficult to access the drive, this time the xlsx files was downloaded and uploaded here on the plataform. We focus again on the geographical data and the case counts

In [44]:
Torito=pd.read_excel(r'CityofToronto_COVID-19_NeighbourhoodData.xlsx')
Torito.fillna(0,inplace=True)

In [45]:
#change column to in (clarified below)
Torito[['Neighbourhood ID']] =Torito[['Neighbourhood ID']].astype(int)
Torito.head()

Neighbourhood ID        Neighbourhood Name  Rate per 100,000 people  \
0               138             Eglinton East               614.682122   
1                47        Don Valley Village               284.647518   
2                38          Lansing-Westgate               303.142786   
3                 9  Edenbridge-Humber Valley               759.575153   
4                44           Flemingdon Park               702.138330   

   Case Count  
0         140  
1          77  
2          49  
3         118  
4         154

We have the same problem with the neighborhoods having a different organization. We proceed similarly, with the coordinates from the oficial database:

In [46]:
with open('Neighbourhoods.geojson') as json_data:
    Bull_data = json.load(json_data)

In [47]:
Bull_data['features'][0]['properties']['AREA_SHORT_CODE']

94

as the neighborhood names are also different, we will compare both databases based on the `Neighborhood ID` and the `AREA_SHORT_CODE`; the latter is an int and the former a double, so it was easier to modify the dataframe than the json file

## 4 - Results

### 4.1 - New York

As a preliminary examination, we draw the COVID data map and on top of it, all the neighborhoods:

In [57]:
map_ny = folium.Map(location=[40.7127281, -74.0060152], zoom_start=10)

folium.Choropleth(geo_data=crownny,
             topojson='objects.collection',
             key_on='feature.properties.MODZCTA',
             data=ny,
             columns=['MODIFIED_ZCTA','COVID_CASE_COUNT'], 
             fill_color='RdBu', 
             fill_opacity=0.7, 
             line_opacity=0.5).add_to(map_ny)

for lat, lng, borough, neighborhood in zip(neighny['Latitude'], neighny['Longitude'], neighny['Borough'], neighny['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_ny)  
map_ny

we observe that although the demographic information differs, we still can make comparisons.

In [71]:
# cluster map
map_clusters = folium.Map(location=[40.7127281, -74.0060152], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyfinal['Latitude'], nyfinal['Longitude'], nyfinal['Neighborhood'], nyfinal['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster) -1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

We intentionally chose 4 clusters (see Discussion below). We mainly obtain two very big and two very small groups:

The first group notoriously consists on bars, restaurants, banks and metro stations; i.e. zones with a lot of people and movement. It doesn't seem to have any geographical tendency, except from Manhattan, in which most the group repressents the northern part

In [59]:
nyfinal.loc[nyfinal['Cluster Labels'] == 0, nyfinal.columns[[1] + list(range(5, nyfinal.shape[1]))]]

Neighborhood 1st Most Common Venue        2nd Most Common Venue  \
0              Wakefield              Pharmacy                 Dessert Shop   
2            Eastchester           Bus Station         Caribbean Restaurant   
7               Woodlawn         Deli / Bodega                          Pub   
8                Norwood           Pizza Place           Chinese Restaurant   
11        Pelham Parkway           Bus Station           Italian Restaurant   
13          Bedford Park                 Diner                  Pizza Place   
14    University Heights           Pizza Place                       Bakery   
15        Morris Heights     Recreation Center                  Pizza Place   
17          East Tremont           Pizza Place               Breakfast Spot   
19          High  Bridge           Bus Station                     Pharmacy   
20               Melrose           Pizza Place                     Pharmacy   
21            Mott Haven    Chinese Restaurant                          Gym   
23              Longwood  Fast Food Restaurant               Sandwich Place   
28           Throgs Neck    Italian Restaurant             Asian Restaurant   
32              Van Nest         Deli / Bodega                  Pizza Place   
33           Morris Park           Pizza Place                 Burger Joint   
34               Belmont    Italian Restaurant                  Pizza Place   
36       North Riverdale           Pizza Place           Italian Restaurant   
38         Schuylerville           Pizza Place                     Pharmacy   
39        Edgewater Park    Italian Restaurant                Deli / Bodega   
40           Castle Hill           Pizza Place                         Park   
41             Olinville         Deli / Bodega         Caribbean Restaurant   
42        Pelham Gardens           Bus Station                     Pharmacy   
43             Concourse         Grocery Store                Deli / Bodega   
45              Edenwald    Chinese Restaurant                   Playground   
48           Sunset Park                  Bank    Latin American Restaurant   
53     Manhattan Terrace        Ice Cream Shop                  Pizza Place   
54              Flatbush  Caribbean Restaurant                Deli / Bodega   
55         Crown Heights           Pizza Place                       Museum   
72         East New York         Deli / Bodega           Child Care Service   
73         Starrett City              Pharmacy                  Pizza Place   
80          Borough Park                  Bank                  Pizza Place   
83           Marine Park         Deli / Bodega               Ice Cream Shop   
89            Ocean Hill         Deli / Bodega                     Bus Stop   
92               Midwood           Pizza Place            Convenience Store   
98         Ocean Parkway           Pizza Place                 Liquor Store   
134               Corona    Mexican Restaurant                  Supermarket   
140            Sunnyside           Pizza Place           Chinese Restaurant   
142              Maspeth                 Diner                  Pizza Place   
144             Glendale   Arts & Crafts Store                Deli / Bodega   
146            Woodhaven         Deli / Bodega                         Park   
149        College Point         Deli / Bodega    Latin American Restaurant   
150           Whitestone       Bubble Tea Shop                  Candy Store   
156            Bellerose         Deli / Bodega           Italian Restaurant   
157    Kew Gardens Hills                  Bank                  Pizza Place   
158        Fresh Meadows           Bus Station                     Pharmacy   
159            Briarwood         Deli / Bodega            Convenience Store   
170         Far Rockaway         Deli / Bodega           Chinese Restaurant   
171        Broad Channel         Deli / Bodega          Sporting Goods Shop   
174           Beechhurst    Chinese Restaurant                

The second group contains bars and restaurants as well, but also shows an important amount of stores and health and fitness venues; although crowded, it represent less activity than group 1

In [60]:
nyfinal.loc[nyfinal['Cluster Labels'] == 1, nyfinal.columns[[1] + list(range(5, nyfinal.shape[1]))]]

Neighborhood      1st Most Common Venue  \
1                   Co-op City                Bus Station   
3                    Fieldston                      Plaza   
4                    Riverdale                       Park   
5                  Kingsbridge                Pizza Place   
6                  Marble Hill                        Gym   
9               Williamsbridge                  Nightclub   
10                  Baychester                 Donut Shop   
12                 City Island         Seafood Restaurant   
16                     Fordham          Mobile Phone Shop   
18                  West Farms                Bus Station   
22                 Port Morris     Furniture / Home Store   
24                 Hunts Point                Pizza Place   
25                  Morrisania              Grocery Store   
26                   Soundview         Chinese Restaurant   
27                Clason Point                       Park   
29                Country Club             Sandwich Place   
30                 Parkchester                Supermarket   
31          Westchester Square       Fast Food Restaurant   
35              Spuyten Duyvil                       Park   
37                  Pelham Bay         Italian Restaurant   
44                   Unionport                 Donut Shop   
46                   Bay Ridge         Italian Restaurant   
47                 Bensonhurst         Chinese Restaurant   
49                  Greenpoint                        Bar   
50                   Gravesend                Pizza Place   
51              Brighton Beach         Russian Restaurant   
52              Sheepshead Bay         Turkish Restaurant   
56               East Flatbush                       Park   
57                  Kensington            Thai Restaurant   
58             Windsor Terrace                       Park   
59            Prospect Heights                        Bar   
60                 Brownsville        Fried Chicken Joint   
61                Williamsburg                Coffee Shop   
62                    Bushwick                        Bar   
63          Bedford Stuyvesant                Coffee Shop   
64            Brooklyn Heights              Deli / Bodega   
65                 Cobble Hill                Pizza Place   
66             Carroll Gardens         Italian Restaurant   
67                    Red Hook         Seafood Restaurant   
68                     Gowanus         Italian Restaurant   
69                 Fort Greene         Italian Restaurant   
70                  Park Slope                Coffee Shop   
71               Cypress Hills  Latin American Restaurant   
74                    Canarsie              Grocery Store   
75                   Flatlands       Caribbean Restaurant   
77             Manhattan Beach                       Café   
78                Coney Island        Monument / Landmark   
79                  Bath Beach                Gas Station   
81               Dyker Heights               Burger Joint   
82             Gerritsen Beach                        Bar   
84                Clinton Hill                Pizza Place   
85                    Sea Gate                Sports Club   
86                    Downtown                Coffee Shop   
87                 Boerum Hill               Dance Studio   
88   Prospect Lefferts Gardens                       Café   
90                   City Line                 Donut Shop   
91                Bergen Beach            Harbor / Marina   
93         Prospect Park South                Pizza Place   
94                  Georgetown                       Bank   
95           East Williamsburg              Deli / Bodega   
96                  North Side                Coffee Shop   
97                  South Side                        Bar   
99               Fort Hamilton                Pizza Place   
100                  Chinatown         Chinese Restaurant   
101         Washington Heights                       

the last two groups consist on a pair of neighborhoods each, however, strikingly uniform and both seemingly more into 'open air' activities

In [61]:
nyfinal.loc[nyfinal['Cluster Labels'] == 2, nyfinal.columns[[1] + list(range(5, nyfinal.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
76    Mill Island                  Pool         Women's Store   
238  Butler Manor        Baseball Field                  Pool   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
76            Fish Market               Exhibit            Eye Doctor   
238           Fish Market               Exhibit            Eye Doctor   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76                Factory    Falafel Restaurant                  Farm   
238               Factory    Falafel Restaurant                  Farm   

    9th Most Common Venue 10th Most Common Venue  
76         Farmers Market   Fast Food Restaurant  
238        Farmers Market   Fast Food Restaurant

In [62]:
nyfinal.loc[nyfinal['Cluster Labels'] == 3, nyfinal.columns[[1] + list(range(5, nyfinal.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192   Somerville                  Park         Women's Store   
203    Todt Hill                  Park         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192           Event Space            Eye Doctor               Factory   
203           Event Space            Eye Doctor               Factory   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192    Falafel Restaurant                  Farm        Farmers Market   
203    Falafel Restaurant                  Farm        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
192  Fast Food Restaurant                  Field  
203  Fast Food Restaurant                  Field

In [63]:
# COVID and clusters:
map_nyk = folium.Map(location=[40.7127281, -74.0060152], zoom_start=10)

folium.Choropleth(geo_data=crownny,
             topojson='objects.collection',
             key_on='feature.properties.MODZCTA',
             data=ny,
             columns=['MODIFIED_ZCTA','COVID_CASE_COUNT'], 
             fill_color='RdBu', 
             fill_opacity=0.7, 
             line_opacity=0.5).add_to(map_nyk)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyfinal['Latitude'], nyfinal['Longitude'], nyfinal['Neighborhood'], nyfinal['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster) -1],
        fill_opacity=0.7).add_to(map_nyk)
    
map_nyk

Interestingly, group 2 seems to fit well with the zones on bright red, corresponding to the lower case count. Following is group 1, that mostly appears on the orange-light red regions (low to mid case count). It doesn't seem to be a particular pattern for the regions with high numbers, nor a specific results for groups 3 and 4. 

### 4.2 - Toronto

In [64]:
map_clusters = folium.Map(location=[43.651070, -79.347015], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(FinalHoods['Latitude'], FinalHoods['Longitude'], FinalHoods['Neighbourhood'], FinalHoods['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster) -1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Here we try 5 clusters. We get a highly dominant group concentrating towards the heart of the city, a mid sized group spread mostly outside of it and 3 individual clusters also at the outskirts:

In [65]:
FinalHoods.loc[FinalHoods['Cluster Labels'] == 0, FinalHoods.columns[[1] + list(range(5, FinalHoods.shape[1]))]]

Borough  Cluster Labels  1st Most Common Venue 2nd Most Common Venue  \
32  Scarborough             0.0  Vietnamese Restaurant        Baseball Field   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
32              Pharmacy                   Zoo  Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
32           Escape Room  Ethiopian Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
32    Falafel Restaurant                   Farm

In [66]:
FinalHoods.loc[FinalHoods['Cluster Labels'] == 1, FinalHoods.columns[[1] + list(range(5, FinalHoods.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
1          North York             1.0            Playground   
8           East York             1.0           Pizza Place   
9    Downtown Toronto             1.0                  Park   
17          Etobicoke             1.0                  Park   
24   Downtown Toronto             1.0              Pharmacy   
25   Downtown Toronto             1.0                  Park   
31       West Toronto             1.0                   Spa   
74    Central Toronto             1.0           Pizza Place   
88          Etobicoke             1.0                  Park   
89          Etobicoke             1.0        Discount Store   
91   Downtown Toronto             1.0                  Park   
93          Etobicoke             1.0              Pharmacy   
94          Etobicoke             1.0                  Park   
96   Downtown Toronto             1.0     Electronics Store   
97   Downtown Toronto             1.0        Discount Store   
101         Etobicoke             1.0           Pizza Place   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1            Burger Joint    Italian Restaurant                  Park   
8          Ice Cream Shop                 Beach        Hardware Store   
9          Ice Cream Shop                  Café       Thai Restaurant   
17            Coffee Shop              Pharmacy        Ice Cream Shop   
24                 Bakery           Pizza Place                  Park   
25               Bus Stop     Convenience Store         Shopping Mall   
31          Shopping Mall                  Park         Grocery Store   
74               Pharmacy                  Park            Food Truck   
88                 Bakery         Grocery Store  Fast Food Restaurant   
89      Convenience Store           Pizza Place              Pharmacy   
91         Ice Cream Shop              Bus Stop         Shopping Mall   
93      Convenience Store                  Café          Skating Rink   
94            Pizza Place                 Hotel                  Bank   
96                 Bakery           Pizza Place                  Bank   
97           Intersection                  Park                Bakery   
101         Grocery Store        Hardware Store        Sandwich Place   

                        5th Most Common Venue 6th Most Common Venue  \
1                              Breakfast Spot                  Food   
8                                  Restaurant                  Park   
9                       General Entertainment                   Gym   
17   Residential Building (Apartment / Condo)         Shopping Mall   
24                              Grocery Store           Coffee Shop   
25                                   Pharmacy          Tennis Court   
31                      Vietnamese Restaurant           Pizza Place   
74                                        Gym        Cosmetics Shop   
88                        Fried Chicken Joint              Pharmacy   
89                                 Print Shop                   Gym   
91                       Gym / Fitness Center    Italian Restaurant   
93                              Shopping Mall           Golf Course   
94                          Fish & Chips Shop            Restaurant   
96                                       Park              Pharmacy   
97                              Auto Workshop           Gas Station   
101                                  Bus Line  Caribbean Restaurant   

           7th Most Common Venue        8th Most Common Venue  \
1           Fast Food Restaurant            Elementary School   
8                     Sports Bar                 Hockey Arena   
9                   Skating Rink                     Gym Pool   
17                Sandwich Place                         Bank   
24                       Butcher  Eastern European Restaurant   
25                Shop & Service                  Coffee Shop   
31                          Bank     

In [67]:
FinalHoods.loc[FinalHoods['Cluster Labels'] == 2, FinalHoods.columns[[1] + list(range(5, FinalHoods.shape[1]))]]

Borough  Cluster Labels   1st Most Common Venue  \
0          North York             2.0                   Trail   
2    Downtown Toronto             2.0             Pizza Place   
4    Downtown Toronto             2.0             Coffee Shop   
5           Etobicoke             2.0          Ice Cream Shop   
6         Scarborough             2.0             Coffee Shop   
7          North York             2.0                Pharmacy   
10         North York             2.0       Electronics Store   
11          Etobicoke             2.0             Pizza Place   
12        Scarborough             2.0      Chinese Restaurant   
13         North York             2.0                Pharmacy   
14          East York             2.0      Chinese Restaurant   
15   Downtown Toronto             2.0      Chinese Restaurant   
18        Scarborough             2.0          Clothing Store   
19       East Toronto             2.0             Gas Station   
21               York             2.0       Korean Restaurant   
22        Scarborough             2.0             Coffee Shop   
23          East York             2.0                    Park   
26        Scarborough             2.0             Coffee Shop   
27         North York             2.0              Restaurant   
28         North York             2.0                    Bank   
29          East York             2.0             Coffee Shop   
30   Downtown Toronto             2.0             Coffee Shop   
33         North York             2.0                   Hotel   
34         North York             2.0             Coffee Shop   
35          East York             2.0    Gym / Fitness Center   
36   Downtown Toronto             2.0                    Park   
37       West Toronto             2.0                     Pub   
38        Scarborough             2.0     Sporting Goods Shop   
39         North York             2.0             Coffee Shop   
40         North York             2.0             Coffee Shop   
41       East Toronto             2.0        Greek Restaurant   
42   Downtown Toronto             2.0       Indian Restaurant   
43       West Toronto             2.0             Coffee Shop   
44        Scarborough             2.0                    Park   
45         North York             2.0             Coffee Shop   
46         North York             2.0             Coffee Shop   
47       East Toronto             2.0      Italian Restaurant   
48   Downtown Toronto             2.0           Grocery Store   
49         North York             2.0             Coffee Shop   
50         North York             2.0             Coffee Shop   
51        Scarborough             2.0                    Café   
52         North York             2.0             Coffee Shop   
53         North York             2.0             Coffee Shop   
54       East Toronto             2.0             Coffee Shop   
55         North York             2.0             Coffee Shop   
56               York             2.0             Coffee Shop   
57         North York             2.0             Coffee Shop   
58        Scarborough             2.0             Coffee Shop   
59         North York             2.0             Coffee Shop   
60         North York             2.0             Coffee Shop   
61    Central Toronto             2.0             Coffee Shop   
62    Central Toronto             2.0             Coffee Shop   
63               York             2.0      Italian Restaurant   
64               York             2.0                    Park   
65        Scarborough             2.0             Coffee Shop   
66         North York             2.0                    Café   
67    Central Toronto             2.0                    Café   
68    Central Toronto             2.0             Coffee Shop   
69       West Toronto             2.0             Coffee Shop   
70          Etobicoke             2.0             Coffee Shop   
71        Scarborough             2.0          Cl

In [68]:
FinalHoods.loc[FinalHoods['Cluster Labels'] == 3, FinalHoods.columns[[1] + list(range(5, FinalHoods.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
20  Downtown Toronto             3.0                  Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
20                  Pool                   Zoo  Fast Food Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
20     Elementary School           Escape Room  Ethiopian Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
20           Event Space    Falafel Restaurant                   Farm

In [69]:
FinalHoods.loc[FinalHoods['Cluster Labels'] == 4, FinalHoods.columns[[1] + list(range(5, FinalHoods.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
102  Etobicoke             4.0                Lounge           Coffee Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
102                   Zoo  Fast Food Restaurant           Escape Room   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
102  Ethiopian Restaurant           Event Space    Falafel Restaurant   

    9th Most Common Venue 10th Most Common Venue  
102                  Farm         Farmers Market

The biggest group consists again on districts mostly containing restaurants, bars and banks. The second most populated includes stores, parks and health and fitness venues. Interestingly, the 3 isolated clusters have a zoo and two are close to an airport

In [70]:
# COVID and clusters
map_tork = folium.Map(location=[43.651070, -79.347015], zoom_start=10)

folium.Choropleth(geo_data=Bull_data,
             key_on='feature.properties.AREA_SHORT_CODE',
             data=Torito,
             columns=['Neighbourhood ID','Case Count'], 
             fill_color='RdBu', 
             fill_opacity=0.7, 
             line_opacity=0.5).add_to(map_tork)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(FinalHoods['Latitude'], FinalHoods['Longitude'], FinalHoods['Neighbourhood'], FinalHoods['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster) -1],
        fill_opacity=0.7).add_to(map_tork)
    
map_tork

Again, the biggest group seems to fit well with the dark red areas, which represent a low case count. Interestingly two of the isolated clusters are part of the zones with higher counts.

## 5 - Discussion

Two main results follow from this work. 

* First, both cities present very similar cluster distribution: two highly dominant groups consisting mostly on bars, restaurants and banks, while the rest of the groups are small, without any particular pattern. From the two dominant groups, the biggest is focused on social activities, while the second includes an important component of health and shopping districts. Clearly, this is related to the center and residential areas of each city, although the existence of two well differentiated central groups was unexpected. 

* Second, there seems to be a tendency between the type of neighborhood the incidence of covid, with the biggest clusters, also being the ones showing more activity have a low incidence, while the isolated ones have the highest. **However**, most likely this is just a reflection of most of the people not living on the city center. A further study taking into consideration population density and, particularly, the presence of hospitals should follow.

## 6 - Conclusion

The main purpose of this modest study was to put into practice the knowledge gained during the course. It includes many simplifications and assumptions that are hard to justify, for the sake of simplification. However, some conclusions can still be extracted, that could be a starting point for further, more serious investigations. 